In [78]:
import nltk
from nltk.corpus import stopwords
import pandas as pd

In [79]:
import os
os.environ["JAVA_HOME"] = "C:\\Program Files\\Java\\jdk-22"

import pyterrier as pt
if not pt.started():
  pt.init()

Data Collection

In [80]:
import pandas as pd

collection = []

categories = ['business', 'entertainment', 'food',
              'graphics', 'historical', 'space', 'sport', 'technologie']

for category in categories:
    for i in range(1, 101):
        filename = f'./archive_2/{category}/{category}_{i}.txt'
        with open(filename, 'r') as f:
            lines = f.readlines()
            for line in lines:
                line = line.strip()
                if line:
                    collection.append({'category': category, 'text': line})

df = pd.DataFrame(collection)
df.to_csv('text.csv', index=False)

In [81]:
df = pd.read_csv('./text.csv')
df

category                                               text
0         business                     Lufthansa flies back to profit
1         business  German airline Lufthansa has returned to profi...
2         business  In a preliminary report, the airline announced...
3         business                   Japanese growth grinds to a halt
4         business  Growth in Japan evaporated in the three months...
...            ...                                                ...
12744  technologie  Consumers swapping old phones for slinkier, di...
12745  technologie  In fact, the numbers of people not taking and ...
12746  technologie  "Also," he said, "they have to simplify the in...
12747  technologie  There are other deeper technical reasons why m...
12748  technologie  No-one wants to take the risk of swamping thes...

[12749 rows x 2 columns]

In [82]:
#check if there is empty rows
df

category                                               text
0         business                     Lufthansa flies back to profit
1         business  German airline Lufthansa has returned to profi...
2         business  In a preliminary report, the airline announced...
3         business                   Japanese growth grinds to a halt
4         business  Growth in Japan evaporated in the three months...
...            ...                                                ...
12744  technologie  Consumers swapping old phones for slinkier, di...
12745  technologie  In fact, the numbers of people not taking and ...
12746  technologie  "Also," he said, "they have to simplify the in...
12747  technologie  There are other deeper technical reasons why m...
12748  technologie  No-one wants to take the risk of swamping thes...

[12749 rows x 2 columns]

Preprocessing

In [83]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer, WordNetLemmatizer

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')





[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\midoh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\midoh\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\midoh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [84]:
stop_words = set(stopwords.words('english'))

def remove_stopwords(text):

    tokens = word_tokenize(text)
    filtered_tokens = [word.lower()
                       for word in tokens if word.lower() not in stop_words]
    print('Tokens are:', tokens, '\n')
    return ' '.join(filtered_tokens)


df['processed_text'] = df['text'].apply(remove_stopwords)

Tokens are: ['Lufthansa', 'flies', 'back', 'to', 'profit'] 

Tokens are: ['German', 'airline', 'Lufthansa', 'has', 'returned', 'to', 'profit', 'in', '2004', 'after', 'posting', 'huge', 'losses', 'in', '2003', '.'] 

Tokens are: ['In', 'a', 'preliminary', 'report', ',', 'the', 'airline', 'announced', 'net', 'profits', 'of', '400m', 'euros', '(', '$', '527.61m', ';', '£274.73m', ')', ',', 'compared', 'with', 'a', 'loss', 'of', '984m', 'euros', 'in', '2003', '.', 'Operating', 'profits', 'were', 'at', '380m', 'euros', ',', 'ten', 'times', 'more', 'than', 'in', '2003', '.', 'Lufthansa', 'was', 'hit', 'in', '2003', 'by', 'tough', 'competition', 'and', 'a', 'dip', 'in', 'demand', 'following', 'the', 'Iraq', 'war', 'and', 'the', 'killer', 'SARS', 'virus', '.', 'It', 'was', 'also', 'hit', 'by', 'troubles', 'at', 'its', 'US', 'catering', 'business', '.', 'Last', 'year', ',', 'Lufthansa', 'showed', 'signs', 'of', 'recovery', 'even', 'as', 'some', 'European', 'and', 'US', 'airlines', 'were', 'teet

In [85]:
stemmer = PorterStemmer()


def Steem_text(text):

    tokens = word_tokenize(text)
    stemmed_tokens = [stemmer.stem(word) for word in tokens]
    return ' '.join(stemmed_tokens)



df['processed_text'] = df['processed_text'].apply(Steem_text)

In [86]:
import re

# a function to clean the df
def clean(text):
  text = re.sub(r"http\S+", " ", text)  # remove urls
  text = re.sub(r"RT ", " ", text)  # remove rt
  text = re.sub(r"@[\w]*", " ", text)  # remove handles
  # remove special characters
  text = re.sub(r"[\.\,\#_\|\:\?\?\/\=]", " ", text)
  text = re.sub(r'\t', ' ', text)  # remove tabs
  text = re.sub(r'\n', ' ', text)  # remove line jump
  text = re.sub(r"\s+", " ", text)  # remove extra white space
  text = text.strip()
  return text


df['processed_text'] = df['processed_text'].apply(clean)

In [87]:
df['docno'] = range(1, len(df)+1)
df['docno'] = df['docno'].apply(str)
df

category                                               text  \
0         business                     Lufthansa flies back to profit   
1         business  German airline Lufthansa has returned to profi...   
2         business  In a preliminary report, the airline announced...   
3         business                   Japanese growth grinds to a halt   
4         business  Growth in Japan evaporated in the three months...   
...            ...                                                ...   
12744  technologie  Consumers swapping old phones for slinkier, di...   
12745  technologie  In fact, the numbers of people not taking and ...   
12746  technologie  "Also," he said, "they have to simplify the in...   
12747  technologie  There are other deeper technical reasons why m...   
12748  technologie  No-one wants to take the risk of swamping thes...   

                                          processed_text  docno  
0                              lufthansa fli back profit      1  
1      german airlin lufthansa return profit 2004 pos...      2  
2      preliminari report airlin announc net profit 4...      3  
3                              japanes growth grind halt      4  
4      growth japan evapor three month septemb spark ...      5  
...                                                  ...    ...  
12744  consum swap old phone slinkier dinkier version...  12745  
12745  fact number peopl take send pictur audio video...  12746  
12746  `` also `` said `` simplifi interfac rocket sc...  12747  
12747  deeper technic reason multimedia messag push s...  12748  
12748  no-on want take risk swamp rel narrow channel ...  12749  

[12749 rows x 4 columns]

Inverted Index

In [88]:
inverted_index = {}

for index, row in df.iterrows():
    doc_id = index + 1
    words = row['text'].split()
    for term in words:
        if term not in inverted_index:
            inverted_index[term] = {}
        if doc_id not in inverted_index[term]:
            inverted_index[term][doc_id] = 0
        inverted_index[term][doc_id] += 1

inverted_index

{'Lufthansa': {1: 1, 2: 1, 3: 3, 212: 1},
 'flies': {1: 1, 10451: 1},
 'back': {1: 1,
  28: 1,
  32: 1,
  39: 1,
  61: 1,
  84: 1,
  103: 1,
  108: 1,
  137: 1,
  166: 1,
  170: 1,
  193: 1,
  208: 1,
  216: 1,
  222: 1,
  272: 1,
  277: 1,
  298: 1,
  340: 1,
  429: 1,
  506: 1,
  637: 1,
  645: 1,
  734: 1,
  809: 1,
  867: 1,
  878: 1,
  952: 1,
  1008: 1,
  1054: 1,
  1101: 1,
  1201: 1,
  1406: 2,
  1459: 1,
  1784: 1,
  1832: 1,
  1840: 1,
  1863: 1,
  2725: 1,
  2769: 1,
  2801: 1,
  2969: 1,
  2988: 1,
  4369: 1,
  4795: 1,
  4830: 1,
  4833: 1,
  4840: 1,
  4897: 1,
  4902: 1,
  4907: 1,
  4936: 1,
  4968: 1,
  4977: 1,
  4980: 1,
  5010: 1,
  5040: 1,
  5046: 2,
  5048: 1,
  5055: 1,
  5056: 1,
  5066: 1,
  5068: 4,
  5093: 1,
  5115: 1,
  5118: 1,
  5136: 1,
  5140: 1,
  5155: 1,
  5168: 2,
  5215: 1,
  5235: 1,
  5271: 1,
  5278: 1,
  5397: 1,
  5416: 1,
  5418: 1,
  5469: 1,
  5515: 1,
  5554: 1,
  5558: 1,
  5591: 1,
  5674: 1,
  5699: 1,
  5713: 1,
  6212: 1,
  6417: 1,


In [89]:
indexer = pt.DFIndexer('C:\\Users\\midoh\\Desktop\\UST-CSAI\\Y2S2\\DSAI 201 (Mining & IR)\\Project\\myFirstIndex', overwrite=True)

index_ref = indexer.index(df["processed_text"], df["docno"])

21:35:37.289 [main] WARN org.terrier.structures.indexing.Indexer - Adding an empty document to the index (1138) - further warnings are suppressed
21:35:40.655 [main] WARN org.terrier.structures.indexing.Indexer - Indexed 44 empty documents
21:35:40.655 [main] ERROR org.terrier.structures.indexing.Indexer - Could not rename index
java.io.IOException: Rename of index structure file 'C:\Users\midoh\Desktop\UST-CSAI\Y2S2\DSAI 201 (Mining & IR)\Project\myFirstIndex/data_1.direct.bf' (exists) to 'C:\Users\midoh\Desktop\UST-CSAI\Y2S2\DSAI 201 (Mining & IR)\Project\myFirstIndex/data.direct.bf' (exists) failed - likely that source file is still open. Possible indexing bug?
	at org.terrier.structures.IndexUtil.renameIndex(IndexUtil.java:379)
	at org.terrier.structures.indexing.Indexer.index(Indexer.java:388)
	at org.terrier.structures.indexing.Indexer.index(Indexer.java:355)


In [90]:
print(index_ref.toString())

index = pt.IndexFactory.of(index_ref)

print(index.getCollectionStatistics().toString())

C:\Users\midoh\Desktop\UST-CSAI\Y2S2\DSAI 201 (Mining & IR)\Project\myFirstIndex/data.properties
Number of documents: 12749
Number of terms: 17725
Number of postings: 165942
Number of fields: 0
Number of tokens: 188085
Field names: []
Positions:   false



In [91]:
for kv in index.getLexicon():
  print("%s -> %s " % (kv.getKey(), kv.getValue().toString()))

0 -> term54 Nt=134 TF=168 maxTF=4 @{0 0 0} 
00 -> term6236 Nt=22 TF=24 maxTF=2 @{0 164 6} 
000 -> term367 Nt=232 TF=350 maxTF=8 @{0 206 4} 
000m -> term16044 Nt=31 TF=41 maxTF=5 @{0 447 4} 
0012 -> term13291 Nt=1 TF=1 maxTF=1 @{0 479 4} 
0028 -> term15892 Nt=1 TF=1 maxTF=1 @{0 482 6} 
0029 -> term14349 Nt=1 TF=1 maxTF=1 @{0 486 2} 
0038 -> term8796 Nt=1 TF=1 maxTF=1 @{0 489 4} 
0065 -> term14566 Nt=1 TF=1 maxTF=1 @{0 492 4} 
007 -> term5706 Nt=1 TF=1 maxTF=1 @{0 495 6} 
0094 -> term8904 Nt=1 TF=1 maxTF=1 @{0 498 2} 
00pm -> term8085 Nt=1 TF=2 maxTF=2 @{0 501 2} 
01 -> term4163 Nt=24 TF=24 maxTF=1 @{0 504 3} 
0100 -> term4691 Nt=1 TF=1 maxTF=1 @{0 550 7} 
0184 -> term8025 Nt=1 TF=1 maxTF=1 @{0 553 3} 
018b -> term15389 Nt=2 TF=2 maxTF=1 @{0 556 3} 
0199 -> term8402 Nt=1 TF=1 maxTF=1 @{0 562 3} 
02 -> term6918 Nt=9 TF=9 maxTF=1 @{0 565 3} 
0200 -> term8421 Nt=1 TF=1 maxTF=1 @{0 585 7} 
0237 -> term7364 Nt=1 TF=1 maxTF=1 @{0 588 7} 
0245 -> term14661 Nt=1 TF=1 maxTF=1 @{0 591 7} 
028 -> t

In [92]:
term = "expect"
term = stemmer.stem(term)

In [93]:
term = "expect"
term = stemmer.stem(term)
try:
    pointer = index.getLexicon()[term]
    posting_list = index.getInvertedIndex().getPostings(pointer)
    if posting_list is not None:
        for posting in posting_list:
            print(posting.toString() + " doclen=%d" %
                  posting.getDocumentLength())
    else:
        print("Posting list for term '%s' is empty" % term)
except KeyError:
    print("Term '%s' not found in the index" % term)

ID(5) TF(1) doclen=32
ID(14) TF(1) doclen=67
ID(21) TF(1) doclen=47
ID(23) TF(1) doclen=3
ID(24) TF(1) doclen=12
ID(26) TF(1) doclen=77
ID(36) TF(1) doclen=15
ID(45) TF(2) doclen=87
ID(56) TF(1) doclen=46
ID(57) TF(1) doclen=22
ID(58) TF(1) doclen=68
ID(60) TF(1) doclen=11
ID(62) TF(1) doclen=38
ID(72) TF(1) doclen=45
ID(101) TF(1) doclen=32
ID(110) TF(1) doclen=44
ID(119) TF(1) doclen=88
ID(131) TF(1) doclen=76
ID(135) TF(1) doclen=36
ID(138) TF(2) doclen=103
ID(144) TF(1) doclen=52
ID(145) TF(1) doclen=47
ID(160) TF(1) doclen=37
ID(164) TF(1) doclen=58
ID(168) TF(1) doclen=80
ID(173) TF(1) doclen=59
ID(196) TF(1) doclen=63
ID(203) TF(1) doclen=49
ID(207) TF(1) doclen=118
ID(247) TF(1) doclen=38
ID(264) TF(1) doclen=64
ID(267) TF(1) doclen=20
ID(271) TF(1) doclen=62
ID(276) TF(1) doclen=21
ID(280) TF(1) doclen=11
ID(284) TF(1) doclen=81
ID(306) TF(1) doclen=28
ID(308) TF(2) doclen=38
ID(309) TF(2) doclen=73
ID(313) TF(1) doclen=29
ID(318) TF(1) doclen=50
ID(319) TF(1) doclen=56
ID(339

In [94]:
di = index.getDirectIndex()
doi = index.getDocumentIndex()
lex = index.getLexicon()
docid = 10  # docids are 0-based

# Get the document entry for the given document id
doc_entry = doi.getDocumentEntry(docid)

# Get the posting list for the document from the direct index
posting_list = di.getPostings(doc_entry)

# Iterate over the posting list and print each term
for posting in posting_list:
    termid = posting.getId()
    lex_entry = lex.getLexiconEntry(termid)
    print(lex_entry.getKey() + " -> " + str(posting) +
          " doclen=%d" % posting.getDocumentLength())

board -> ID(30) TF(1) doclen=14
chief -> ID(173) TF(1) doclen=14
lie -> ID(178) TF(1) doclen=14
admit -> ID(180) TF(1) doclen=14
worldcom -> ID(181) TF(1) doclen=14
member -> ID(182) TF(1) doclen=14
york -> ID(183) TF(1) doclen=14
fellow -> ID(184) TF(1) doclen=14
firm -> ID(185) TF(1) doclen=14
financ -> ID(186) TF(1) doclen=14
new -> ID(187) TF(1) doclen=14
telecom -> ID(188) TF(1) doclen=14
offic -> ID(189) TF(1) doclen=14
court -> ID(190) TF(1) doclen=14


In [95]:
df

category                                               text  \
0         business                     Lufthansa flies back to profit   
1         business  German airline Lufthansa has returned to profi...   
2         business  In a preliminary report, the airline announced...   
3         business                   Japanese growth grinds to a halt   
4         business  Growth in Japan evaporated in the three months...   
...            ...                                                ...   
12744  technologie  Consumers swapping old phones for slinkier, di...   
12745  technologie  In fact, the numbers of people not taking and ...   
12746  technologie  "Also," he said, "they have to simplify the in...   
12747  technologie  There are other deeper technical reasons why m...   
12748  technologie  No-one wants to take the risk of swamping thes...   

                                          processed_text  docno  
0                              lufthansa fli back profit      1  
1      german airlin lufthansa return profit 2004 pos...      2  
2      preliminari report airlin announc net profit 4...      3  
3                              japanes growth grind halt      4  
4      growth japan evapor three month septemb spark ...      5  
...                                                  ...    ...  
12744  consum swap old phone slinkier dinkier version...  12745  
12745  fact number peopl take send pictur audio video...  12746  
12746  `` also `` said `` simplifi interfac rocket sc...  12747  
12747  deeper technic reason multimedia messag push s...  12748  
12748  no-on want take risk swamp rel narrow channel ...  12749  

[12749 rows x 4 columns]